# **BUSINESS CASE 2: SIEMENS ADVANTA SALES FORECASTING**  


## 🎓 Master’s Program in Data Science & Advanced Analytics 
**Nova IMS** | March 2025   
**Course:** Business Cases with Data Science

## 👥 Team **Group A**  
- **Alice Viegas** | 20240572  
- **Bernardo Faria** | 20240579  
- **Dinis Pinto** | 20240612  
- **Daan van Holten** | 20240681
- **Philippe Dutranoit** | 20240518

## 📊 Goal of the notebook

in this notebook we make the build and test the models for forcasting

# Imports

In [2]:
import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from datetime import datetime
from sklearn.model_selection import TimeSeriesSplit, GridSearchCV
import itertools
from sklearn.metrics import mean_squared_error
from xgboost import XGBRegressor
from prophet import Prophet


from Model_Functions import *

import importlib
imported_module = importlib.import_module("Model_Functions")
importlib.reload(imported_module)


<module 'Model_Functions' from '/Users/philippedutranoit/document_ordi/nova/business_case_for_data_sciense/cases/BC_DA_Siemens/Notebooks/Model_Functions.py'>

In [3]:
sales_agg1 = pd.read_csv('../data/sales_agg1.csv').set_index('DATE')
sales_agg3 = pd.read_csv('../data/sales_agg3.csv').set_index('DATE')
sales_agg4 = pd.read_csv('../data/sales_agg4.csv').set_index('DATE')
sales_agg5 = pd.read_csv('../data/sales_agg5.csv').set_index('DATE')
sales_agg6 = pd.read_csv('../data/sales_agg6.csv').set_index('DATE')
sales_agg8 = pd.read_csv('../data/sales_agg8.csv').set_index('DATE')
sales_agg9 = pd.read_csv('../data/sales_agg9.csv').set_index('DATE')
sales_agg11 = pd.read_csv('../data/sales_agg11.csv').set_index('DATE')
sales_agg12 = pd.read_csv('../data/sales_agg12.csv').set_index('DATE')
sales_agg13 = pd.read_csv('../data/sales_agg13.csv').set_index('DATE')
sales_agg14 = pd.read_csv('../data/sales_agg14.csv').set_index('DATE')
sales_agg16 = pd.read_csv('../data/sales_agg16.csv').set_index('DATE')
sales_agg20 = pd.read_csv('../data/sales_agg20.csv').set_index('DATE')
sales_agg36 = pd.read_csv('../data/sales_agg36.csv').set_index('DATE')

# extract the selected features list build in the feature selection step
selected_features_1 = pd.read_csv('../data/selected_features_1.csv')['selected_features'].tolist()
selected_features_3 = pd.read_csv('../data/selected_features_3.csv')['selected_features'].tolist()
selected_features_4 = pd.read_csv('../data/selected_features_4.csv')['selected_features'].tolist()
selected_features_5 = pd.read_csv('../data/selected_features_5.csv')['selected_features'].tolist()
selected_features_6 = pd.read_csv('../data/selected_features_6.csv')['selected_features'].tolist()
selected_features_8 = pd.read_csv('../data/selected_features_8.csv')['selected_features'].tolist()
selected_features_9 = pd.read_csv('../data/selected_features_9.csv')['selected_features'].tolist()
selected_features_11 = pd.read_csv('../data/selected_features_11.csv')['selected_features'].tolist()
selected_features_12 = pd.read_csv('../data/selected_features_12.csv')['selected_features'].tolist()
selected_features_13 = pd.read_csv('../data/selected_features_13.csv')['selected_features'].tolist()
selected_features_14 = pd.read_csv('../data/selected_features_14.csv')['selected_features'].tolist()
selected_features_16 = pd.read_csv('../data/selected_features_16.csv')['selected_features'].tolist()
selected_features_20 = pd.read_csv('../data/selected_features_20.csv')['selected_features'].tolist()
selected_features_36 = pd.read_csv('../data/selected_features_36.csv')['selected_features'].tolist()


# load the market data
df_market = pd.read_csv('../data/Market_data_predicted.csv').set_index('date')
test_set = pd.read_csv('../Data/Case2_Test Set Template.csv', sep=';')
print(sales_agg1.head())
df_market.head()



               Sales_EUR
DATE                    
2018-10-01  3.609892e+07
2018-11-01  3.699427e+07
2018-12-01  3.788961e+07
2019-01-01  2.772815e+07
2019-02-01  3.479316e+07


MAB_ELE_PRO156  MAB_ELE_SHP156  MAB_ELE_SHP250  MAB_ELE_PRO392  \
date                                                                         
2004-02-01       16.940704       16.940704       83.458866      109.334010   
2004-03-01       23.711852       23.711852      106.168192      140.884616   
2004-04-01       24.435235       24.435235       92.007646      105.853579   
2004-05-01       23.708115       23.708115       85.696486      101.864777   
2004-06-01       27.009138       27.009138      106.641482      120.332920   

            MAB_ELE_SHP392  MAB_ELE_PRO756  MAB_ELE_SHP756  MAB_ELE_PRO826  \
date                                                                         
2004-02-01      110.495272       86.074496       80.962532      111.353812   
2004-03-01      144.686166       86.038258       80.912352      127.558608   
2004-04-01      102.655769       85.997063       80.857863      108.732297   
2004-05-01      100.305285       85.951483       80.800601      110.645200   
2004-06-01      119.616380       85.902640       80.742724      122.020960   

            MAB_ELE_SHP826  MAB_ELE_SHP840  ...  PRI27380_org  PRI27250_org  \
date                                        ...                               
2004-02-01       77.766367       90.442749  ...     93.020027     96.864647   
2004-03-01       77.829225       90.580357  ...     93.540268     96.864653   
2004-04-01       77.904642       90.751805  ...     93.852425     96.864659   
2004-05-01       77.993606       90.961426  ...     93.852425     96.864666   
2004-06-01       78.096995       91.213203  ...     93.956467     96.864672   

            PRI27276_org  PRO28756_org  PRO28392_org  PRO271000_org  \
date                                                                  
2004-02-01     93.230453     96.177481    110.890034      91.390440   
2004-03-01     93.335678     96.250927    141.176853      91.511498   
2004-04-01     93.440903     96.330211    105.648765      91.666790   
2004-05-01     93.546127     96.413549    101.990361      91.861457   
2004-06-01     93.440903     96.499291    122.136575      92.100289   

            PRO27756_org  PRO27826_org  PRO27392_org  PRO27276_org  
date                                                                
2004-02-01     68.677657    120.706516    106.161262     85.913200  
2004-03-01     68.452548    138.309550    140.288741     97.670815  
2004-04-01     68.203892    115.557330    106.271197     87.253983  
2004-05-01     67.936322    119.269534    101.608710     84.675552  
2004-06-01     67.655734    128.849416    116.655248     95.401802  

[5 rows x 24 columns]

In [4]:
test_set

Month Year Mapped_GCK  Sales_EUR
0       Mai 22         #3        NaN
1       Jun 22         #3        NaN
2       Jul 22         #3        NaN
3       Aug 22         #3        NaN
4       Sep 22         #3        NaN
..         ...        ...        ...
135     Okt 22         #1        NaN
136     Nov 22         #1        NaN
137     Dez 22         #1        NaN
138     Jan 23         #1        NaN
139     Feb 23         #1        NaN

[140 rows x 3 columns]

In [5]:
month_map = {
    "Jan": 1,
    "Feb": 2,
    "Mai": 3,
    "Jun": 6,
    "Jul": 7,
    "Aug": 8,
    "Sep": 9,
    "Okt": 10,
    "Nov": 11,
    "Dez": 12
}

# Apply conversion safely
test_set['Month Year'] = test_set['Month Year'].apply(parse_month_year)

# Preparation 

## Create the lag market data feature needed for the model

In [6]:
df_market = create_lag_features(df_market, 6)
df_market.head()

/Users/philippedutranoit/document_ordi/nova/business_case_for_data_sciense/cases/BC_DA_Siemens/Notebooks/Model_Functions.py:53: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{col}_lag_{lag}'] = df[col].shift(lag)
/Users/philippedutranoit/document_ordi/nova/business_case_for_data_sciense/cases/BC_DA_Siemens/Notebooks/Model_Functions.py:53: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{col}_lag_{lag}'] = df[col].shift(lag)
/Users/philippedutranoit/document_ordi/nova/business_case_for_data_sciense/cases/BC_DA_Siemens/Not

MAB_ELE_PRO156  MAB_ELE_SHP156  MAB_ELE_SHP250  MAB_ELE_PRO392  \
date                                                                         
2004-02-01       16.940704       16.940704       83.458866      109.334010   
2004-03-01       23.711852       23.711852      106.168192      140.884616   
2004-04-01       24.435235       24.435235       92.007646      105.853579   
2004-05-01       23.708115       23.708115       85.696486      101.864777   
2004-06-01       27.009138       27.009138      106.641482      120.332920   

            MAB_ELE_SHP392  MAB_ELE_PRO756  MAB_ELE_SHP756  MAB_ELE_PRO826  \
date                                                                         
2004-02-01      110.495272       86.074496       80.962532      111.353812   
2004-03-01      144.686166       86.038258       80.912352      127.558608   
2004-04-01      102.655769       85.997063       80.857863      108.732297   
2004-05-01      100.305285       85.951483       80.800601      110.645200   
2004-06-01      119.616380       85.902640       80.742724      122.020960   

            MAB_ELE_SHP826  MAB_ELE_SHP840  ...  PRI27380_org_lag_6  \
date                                        ...                       
2004-02-01       77.766367       90.442749  ...                 NaN   
2004-03-01       77.829225       90.580357  ...                 NaN   
2004-04-01       77.904642       90.751805  ...                 NaN   
2004-05-01       77.993606       90.961426  ...                 NaN   
2004-06-01       78.096995       91.213203  ...                 NaN   

            PRI27250_org_lag_6  PRI27276_org_lag_6  PRO28756_org_lag_6  \
date                                                                     
2004-02-01                 NaN                 NaN                 NaN   
2004-03-01                 NaN                 NaN                 NaN   
2004-04-01                 NaN                 NaN                 NaN   
2004-05-01                 NaN                 NaN                 NaN   
2004-06-01                 NaN                 NaN                 NaN   

            PRO28392_org_lag_6  PRO271000_org_lag_6  PRO27756_org_lag_6  \
date                                                                      
2004-02-01                 NaN                  NaN                 NaN   
2004-03-01                 NaN                  NaN                 NaN   
2004-04-01                 NaN                  NaN                 NaN   
2004-05-01                 NaN                  NaN                 NaN   
2004-06-01                 NaN                  NaN                 NaN   

            PRO27826_org_lag_6  PRO27392_org_lag_6  PRO27276_org_lag_6  
date                                                                    
2004-02-01                 NaN                 NaN                 NaN  
2004-03-01                 NaN                 NaN                 NaN  
2004-04-01                 NaN                 NaN                 NaN  
2004-05-01                 NaN                 NaN                 NaN  
2004-06-01                 NaN                 NaN                 NaN  

[5 rows x 168 columns]

## Created lagged sales features needed for the model

In [7]:
sales_agg_with_lag1 = create_lag_features(sales_agg1, 10)
sales_agg_with_lag3 = create_lag_features(sales_agg3, 10)
sales_agg_with_lag4 = create_lag_features(sales_agg4, 10)
sales_agg_with_lag5 = create_lag_features(sales_agg5, 10)
sales_agg_with_lag6 = create_lag_features(sales_agg6, 10)
sales_agg_with_lag8 = create_lag_features(sales_agg8, 10)
sales_agg_with_lag9 = create_lag_features(sales_agg9, 10)
sales_agg_with_lag11 = create_lag_features(sales_agg11, 10)
sales_agg_with_lag12 = create_lag_features(sales_agg12, 10)
sales_agg_with_lag13 = create_lag_features(sales_agg13, 10)
sales_agg_with_lag14 = create_lag_features(sales_agg14, 10)
sales_agg_with_lag16 = create_lag_features(sales_agg16, 10)
sales_agg_with_lag20 = create_lag_features(sales_agg20, 10)
sales_agg_with_lag36 = create_lag_features(sales_agg36, 10)

## Define the parameter grid to run

In [8]:
xgboost_param_grid = {
    'n_estimators': [100, 200],
    'max_depth': [5, 7],
    'learning_rate': [0.01, 0.1, 0.3],
    'subsample': [0.5, 0.7],
    'colsample_bytree': [0.5, 0.7, 1],
    'gamma': [0, 0.1, 0.3],
    'reg_alpha': [0, 0.1, 0.3],
    'reg_lambda': [0, 0.1, 0.3]
}

prophet_param_grid = {
    'seasonality_mode': ['additive', 'multiplicative'],
    'yearly_seasonality': [True, False],
    'weekly_seasonality': [True, False],
    'daily_seasonality': [True, False],
    'seasonality_prior_scale': [0.1, 1.0, 10.0],
    'changepoint_prior_scale': [0.01, 0.1, 0.5]
}

# Product 1

In [9]:
# selecte only the features that are selected in the feature selection step
df_market_1 = df_market[selected_features_1]
df_market_1.head()

PRO27826_org_lag_1  PRO27826_org  MAB_ELE_PRO756_lag_1  \
date                                                                 
2004-02-01                 NaN    120.706516                   NaN   
2004-03-01          120.706516    138.309550             86.074496   
2004-04-01          138.309550    115.557330             86.038258   
2004-05-01          115.557330    119.269534             85.997063   
2004-06-01          119.269534    128.849416             85.951483   

            PRI27380_org  PRO271000_org_lag_5  PRO27392_org_lag_3  \
date                                                                
2004-02-01     93.020027                  NaN                 NaN   
2004-03-01     93.540268                  NaN                 NaN   
2004-04-01     93.852425                  NaN                 NaN   
2004-05-01     93.852425                  NaN          106.161262   
2004-06-01     93.956467                  NaN          140.288741   

            PRO28392_org_lag_6  
date                            
2004-02-01                 NaN  
2004-03-01                 NaN  
2004-04-01                 NaN  
2004-05-01                 NaN  
2004-06-01                 NaN

## Xgboost

In [10]:
X_train, X_val, y_train, y_val = train_val_split(sales_agg_with_lag1, df_market_1, train_size = 0.8)

X_val.info() 

xgboost_best_model_1, xgboost_best_params_1, xgboost_best_rmse_1 = model_evaluation_XGboost(X_train,
                                                                                             y_train, 
                                                                                             X_val, y_val, 
                                                                                             xgboost_param_grid)

print("Best Params:", xgboost_best_params_1)
print("Validation RMSE:", xgboost_best_rmse_1)



<class 'pandas.core.frame.DataFrame'>
Index: 9 entries, 2021-08-01 to 2022-04-01
Data columns (total 17 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   Sales_EUR_lag_1       9 non-null      float64
 1   Sales_EUR_lag_2       9 non-null      float64
 2   Sales_EUR_lag_3       9 non-null      float64
 3   Sales_EUR_lag_4       9 non-null      float64
 4   Sales_EUR_lag_5       9 non-null      float64
 5   Sales_EUR_lag_6       9 non-null      float64
 6   Sales_EUR_lag_7       9 non-null      float64
 7   Sales_EUR_lag_8       9 non-null      float64
 8   Sales_EUR_lag_9       9 non-null      float64
 9   Sales_EUR_lag_10      9 non-null      float64
 10  PRO27826_org_lag_1    9 non-null      float64
 11  PRO27826_org          9 non-null      float64
 12  MAB_ELE_PRO756_lag_1  9 non-null      float64
 13  PRI27380_org          9 non-null      float64
 14  PRO271000_org_lag_5   9 non-null      float64
 15  PRO27392_org_l

## Prophet

In [11]:
prophet_best_model_1, prophet_best_params_1, prophet_best_rmse_1 = model_evaluation_prophet(X_train,
                                                                                             y_train, 
                                                                                             X_val, 
                                                                                             y_val, 
                                                                                             prophet_param_grid)

print("Best Params:", prophet_best_params_1)

print("Validation RMSE:", prophet_best_rmse_1)

15:37:59 - cmdstanpy - INFO - Chain [1] start processing
15:38:00 - cmdstanpy - INFO - Chain [1] done processing
15:38:00 - cmdstanpy - INFO - Chain [1] start processing
15:38:00 - cmdstanpy - INFO - Chain [1] done processing
15:38:00 - cmdstanpy - INFO - Chain [1] start processing


Params: {'seasonality_mode': 'additive', 'yearly_seasonality': True, 'weekly_seasonality': True, 'daily_seasonality': True, 'seasonality_prior_scale': 0.1, 'changepoint_prior_scale': 0.01} => RMSE: 5503348.8019
Params: {'seasonality_mode': 'additive', 'yearly_seasonality': True, 'weekly_seasonality': True, 'daily_seasonality': True, 'seasonality_prior_scale': 0.1, 'changepoint_prior_scale': 0.1} => RMSE: 10118173.9628


15:38:00 - cmdstanpy - INFO - Chain [1] done processing
15:38:00 - cmdstanpy - INFO - Chain [1] start processing
15:38:00 - cmdstanpy - INFO - Chain [1] done processing
15:38:00 - cmdstanpy - INFO - Chain [1] start processing


Params: {'seasonality_mode': 'additive', 'yearly_seasonality': True, 'weekly_seasonality': True, 'daily_seasonality': True, 'seasonality_prior_scale': 0.1, 'changepoint_prior_scale': 0.5} => RMSE: 14585959.4522
Params: {'seasonality_mode': 'additive', 'yearly_seasonality': True, 'weekly_seasonality': True, 'daily_seasonality': True, 'seasonality_prior_scale': 1.0, 'changepoint_prior_scale': 0.01} => RMSE: 17834572.8573


15:38:15 - cmdstanpy - INFO - Chain [1] done processing
15:38:17 - cmdstanpy - INFO - Chain [1] start processing


...

Params: {'seasonality_mode': 'multiplicative', 'yearly_seasonality': False, 'weekly_seasonality': False, 'daily_seasonality': False, 'seasonality_prior_scale': 0.1, 'changepoint_prior_scale': 0.5} => RMSE: 3669936.6345
Params: {'seasonality_mode': 'multiplicative', 'yearly_seasonality': False, 'weekly_seasonality': False, 'daily_seasonality': False, 'seasonality_prior_scale': 1.0, 'changepoint_prior_scale': 0.01} => RMSE: 3689102.8841
Params: {'seasonality_mode': 'multiplicative', 'yearly_seasonality': False, 'weekly_seasonality': False, 'daily_seasonality': False, 'seasonality_prior_scale': 1.0, 'changepoint_prior_scale': 0.1} => RMSE: 3697621.0274


15:42:45 - cmdstanpy - INFO - Chain [1] done processing
15:42:45 - cmdstanpy - INFO - Chain [1] start processing
15:42:45 - cmdstanpy - INFO - Chain [1] done processing
15:42:45 - cmdstanpy - INFO - Chain [1] start processing
15:42:45 - cmdstanpy - INFO - Chain [1] done processing
15:42:45 - cmdstanpy - INFO - Chain [1] start processing


Params: {'seasonality_mode': 'multiplicative', 'yearly_seasonality': False, 'weekly_seasonality': False, 'daily_seasonality': False, 'seasonality_prior_scale': 1.0, 'changepoint_prior_scale': 0.5} => RMSE: 3669936.6345
Params: {'seasonality_mode': 'multiplicative', 'yearly_seasonality': False, 'weekly_seasonality': False, 'daily_seasonality': False, 'seasonality_prior_scale': 10.0, 'changepoint_prior_scale': 0.01} => RMSE: 3689102.8841
Params: {'seasonality_mode': 'multiplicative', 'yearly_seasonality': False, 'weekly_seasonality': False, 'daily_seasonality': False, 'seasonality_prior_scale': 10.0, 'changepoint_prior_scale': 0.1} => RMSE: 3697621.0274


15:42:45 - cmdstanpy - INFO - Chain [1] done processing


Params: {'seasonality_mode': 'multiplicative', 'yearly_seasonality': False, 'weekly_seasonality': False, 'daily_seasonality': False, 'seasonality_prior_scale': 10.0, 'changepoint_prior_scale': 0.5} => RMSE: 3669936.6345
Best Params: {'seasonality_mode': 'multiplicative', 'yearly_seasonality': False, 'weekly_seasonality': False, 'daily_seasonality': True, 'seasonality_prior_scale': 1.0, 'changepoint_prior_scale': 0.5}
Validation RMSE: 3274042.581357753


## Final prediction

In [12]:
best_model, best_params, best_rmse, best_model_name = select_best_model(
    prophet_best_model_1, prophet_best_params_1, prophet_best_rmse_1, "Prophet",
    xgboost_best_model_1, xgboost_best_params_1, xgboost_best_rmse_1, "XGBoost"
)

print(f"Best Model: {best_model_name}")
print("Best Parameters:", best_params)
print("Best RMSE:", best_rmse)

Best Model: XGBoost
Best Parameters: {'n_estimators': 100, 'max_depth': 7, 'learning_rate': 0.3, 'subsample': 0.5, 'colsample_bytree': 0.7, 'gamma': 0, 'reg_alpha': 0, 'reg_lambda': 0.3}
Best RMSE: 2361559.0737925945


In [18]:
def sequential_forecast(best_model_name, best_model, df_market, Sales_agg, test_set, forecast_horizon=10):
    """
    Performs a sequential forecast using the selected best model.
    
    Args:
        best_model_name (str): Either "Prophet" or "XGBoost".
        best_model: Trained forecasting model.
        df_market (DataFrame): Market data including future values.
            Its index must be a datetime index.
        Sales_agg (DataFrame): Historical sales data.
            Its index must be a datetime index and include a 'y' column.
        test_set (DataFrame): Actual values for validation.
            Its index must be a datetime index.
        forecast_horizon (int): Number of months to predict.
    
    Returns:
        DataFrame: Forecast results merged with test_set for comparison.
    """
    # Work on a copy to avoid modifying original data
    sales_history = Sales_agg.copy()
    
    # Ensure the index is a DatetimeIndex
    if not isinstance(sales_history.index, pd.DatetimeIndex):
        sales_history.index = pd.to_datetime(sales_history.index)
    
    predictions = []

    for step in range(forecast_horizon):
        # Create lag features (assumed create_lag_features considers original columns only)
        sales_history = create_lag_features(sales_history, 10)
        
        # Merge sales_history with market data on index
        current_data = sales_history.merge(df_market, left_index=True, right_index=True, how='inner')
        # Convert index into a column called 'ds'
        current_data = current_data.reset_index().rename(columns={'index': 'ds'})
        
        # Determine the forecast date: last available date + 1 month
        last_date = current_data['ds'].max()
        next_date = last_date + pd.DateOffset(months=1)
        
        if best_model_name == "Prophet":
            # Get market features for the next date from df_market using its index
            next_df = df_market.loc[[next_date]].copy()
            if next_df.empty:
                print(f"No market data for {next_date}. Forecast stopped.")
                break
            # Convert index to 'ds' as Prophet requires
            next_df = next_df.reset_index().rename(columns={'index': 'ds'})
            
            # Predict using Prophet: use 'ds' plus all other regressors
            forecast = best_model.predict(next_df[['ds'] + [col for col in next_df.columns if col != 'ds']])
            y_pred = forecast['yhat'].iloc[0]
            predictions.append({'ds': next_date, 'y_pred': y_pred})
        
        elif best_model_name == "XGBoost":
            # For XGBoost, get the row corresponding to next_date from the merged data
            next_data = current_data[current_data['ds'] == next_date]
            if next_data.empty:
                print(f"No combined data for {next_date}. Forecast stopped.")
                break
            # Assume features are all columns except 'ds' and the target 'y'
            X_input = next_data.drop(columns=['ds', 'y'])
            y_pred = best_model.predict(X_input)[0]
            predictions.append({'ds': next_date, 'y_pred': y_pred})
        
        else:
            raise ValueError("Invalid model name. Choose 'Prophet' or 'XGBoost'.")
        
        # Append the prediction to sales_history so future lag features are updated
        new_row = pd.DataFrame({'y': [y_pred]}, index=[next_date])
        sales_history = pd.concat([sales_history, new_row])
    
    pred_df = pd.DataFrame(predictions)
    
    # Prepare test_set by converting its index to 'ds'
    test_set = test_set.reset_index().rename(columns={'index':'ds'})
    test_merged = test_set[['ds', 'y']].rename(columns={'y': 'y_actual'})
    result = pred_df.merge(test_merged, on='ds', how='left')

    # Plot forecast vs actual
    plt.figure(figsize=(10, 6))
    plt.plot(result['ds'], result['y_actual'], label='Actual', color='blue', marker='o')
    plt.plot(result['ds'], result['y_pred'], label='Predicted', color='red', linestyle='--', marker='x')
    plt.title('Forecast vs Actual')
    plt.xlabel('Date')
    plt.ylabel('Sales')
    plt.legend()
    plt.grid(True)
    plt.tight_layout()
    plt.show()

    return result

In [19]:
sequential_forecast(best_model_name, best_model, df_market, sales_agg1, test_set, forecast_horizon=10)

/Users/philippedutranoit/document_ordi/nova/business_case_for_data_sciense/cases/BC_DA_Siemens/Notebooks/Model_Functions.py:53: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{col}_lag_{lag}'] = df[col].shift(lag)
/Users/philippedutranoit/document_ordi/nova/business_case_for_data_sciense/cases/BC_DA_Siemens/Notebooks/Model_Functions.py:53: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{col}_lag_{lag}'] = df[col].shift(lag)
/Users/philippedutranoit/document_ordi/nova/business_case_for_data_sciense/cases/BC_DA_Siemens/Not

TypeError: unsupported operand type(s) for +: 'float' and 'DateOffset'